**Import Library**

In [73]:
import pandas as pd              # data manipulation
import numpy as np               # numerical operations
import matplotlib.pyplot as plt  # plotting
import seaborn as sns            # statistical visuals
import plotly.express as px  # interactive visuals
import calendar             # month name handling   
from matplotlib.ticker import StrMethodFormatter  # format y-axis labels

import requests                  # download data
import zipfile, os                 # handle zip files
import io                        # in-memory file handling
from datetime import datetime    # date/time handling

from mlxtend.frequent_patterns import apriori, association_rules  # market basket analysis
from sklearn.preprocessing import StandardScaler  # feature scaling
from sklearn.cluster import KMeans                # clustering

import warnings
warnings.filterwarnings('ignore')  # suppress warnings

print("Libraries imported.")

Libraries imported.


**Download Dataset from UCI**

In [5]:
# Download the zip file
# Absolute path where you want to save the dataset
save_path = "/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/data"
url = "https://archive.ics.uci.edu/static/public/352/online+retail.zip"
r = requests.get(url)
zip_path = os.path.join(save_path, "online_retail.zip")
with open(zip_path, "wb") as f:
    f.write(r.content)
# Extract the zip file
with zipfile.ZipFile(zip_path, 'r') as z:
    z.extractall(save_path)

# List extracted files
print("Files in data folder:")
print(os.listdir(save_path))

KeyboardInterrupt: 

**Load Data & Initial Inspection**

In [6]:
df = pd.read_excel("/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/data/Online Retail.xlsx")
print(f"Shape: {df.shape}")
df.head()

Shape: (541909, 8)


InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate  UnitPrice  CustomerID         Country  
0 2010-12-01 08:26:00       2.55     17850.0  United Kingdom  
1 2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
2 2010-12-01 08:26:00       2.75     17850.0  United Kingdom  
3 2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
4 2010-12-01 08:26:00       3.39     17850.0  United Kingdom

**Auto EDA**

In [7]:
from ydata_profiling import ProfileReport

profile = ProfileReport(df, title='Initial Data Scan', minimal=True)
profile.to_notebook_iframe()

print("Dataset shape:", df.shape)
print("\nData types:")
print(df.dtypes)
print("\nMissing values:")
print(df.isna().sum())



Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 8/8 [00:00<00:00, 106.22it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Dataset shape: (541909, 8)

Data types:
InvoiceNo              object
StockCode              object
Description            object
Quantity                int64
InvoiceDate    datetime64[ns]
UnitPrice             float64
CustomerID            float64
Country                object
dtype: object

Missing values:
InvoiceNo           0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
UnitPrice           0
CustomerID     135080
Country             0
dtype: int64


In [8]:
#viewing rows without CustomerID (required for RFM)
df[df['CustomerID'].isnull()]

InvoiceNo StockCode                      Description  Quantity  \
622       536414     22139                              NaN        56   
1443      536544     21773  DECORATIVE ROSE BATHROOM BOTTLE         1   
1444      536544     21774  DECORATIVE CATS BATHROOM BOTTLE         2   
1445      536544     21786               POLKADOT RAIN HAT          4   
1446      536544     21787            RAIN PONCHO RETROSPOT         2   
...          ...       ...                              ...       ...   
541536    581498    85099B          JUMBO BAG RED RETROSPOT         5   
541537    581498    85099C   JUMBO  BAG BAROQUE BLACK WHITE         4   
541538    581498     85150    LADIES & GENTLEMEN METAL SIGN         1   
541539    581498     85174                S/4 CACTI CANDLES         1   
541540    581498       DOT                   DOTCOM POSTAGE         1   

               InvoiceDate  UnitPrice  CustomerID         Country  
622    2010-12-01 11:52:00       0.00         NaN  United Kingdom  
1443   2010-12-01 14:32:00       2.51         NaN  United Kingdom  
1444   2010-12-01 14:32:00       2.51         NaN  United Kingdom  
1445   2010-12-01 14:32:00       0.85         NaN  United Kingdom  
1446   2010-12-01 14:32:00       1.66         NaN  United Kingdom  
...                    ...        ...         ...             ...  
541536 2011-12-09 10:26:00       4.13         NaN  United Kingdom  
541537 2011-12-09 10:26:00       4.13         NaN  United Kingdom  
541538 2011-12-09 10:26:00       4.96         NaN  United Kingdom  
541539 2011-12-09 10:26:00      10.79         NaN  United Kingdom  
541540 2011-12-09 10:26:00    1714.17         NaN  United Kingdom  

[135080 rows x 8 columns]

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541909 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   InvoiceNo    541909 non-null  object        
 1   StockCode    541909 non-null  object        
 2   Description  540455 non-null  object        
 3   Quantity     541909 non-null  int64         
 4   InvoiceDate  541909 non-null  datetime64[ns]
 5   UnitPrice    541909 non-null  float64       
 6   CustomerID   406829 non-null  float64       
 7   Country      541909 non-null  object        
dtypes: datetime64[ns](1), float64(2), int64(1), object(4)
memory usage: 33.1+ MB


In [10]:
df.loc[df.Country == 'United Kingdom']

InvoiceNo StockCode                          Description  Quantity  \
0         536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1         536365     71053                  WHITE METAL LANTERN         6   
2         536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3         536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4         536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   
...          ...       ...                                  ...       ...   
541889    581585     22466       FAIRY TALE COTTAGE NIGHT LIGHT        12   
541890    581586     22061  LARGE CAKE STAND  HANGING STRAWBERY         8   
541891    581586     23275     SET OF 3 HANGING OWLS OLLIE BEAK        24   
541892    581586     21217        RED RETROSPOT ROUND CAKE TINS        24   
541893    581586     20685                DOORMAT RED RETROSPOT        10   

               InvoiceDate  UnitPrice  CustomerID         Country  
0      2010-12-01 08:26:00       2.55     17850.0  United Kingdom  
1      2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
2      2010-12-01 08:26:00       2.75     17850.0  United Kingdom  
3      2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
4      2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
...                    ...        ...         ...             ...  
541889 2011-12-09 12:31:00       1.95     15804.0  United Kingdom  
541890 2011-12-09 12:49:00       2.95     13113.0  United Kingdom  
541891 2011-12-09 12:49:00       1.25     13113.0  United Kingdom  
541892 2011-12-09 12:49:00       8.95     13113.0  United Kingdom  
541893 2011-12-09 12:49:00       7.08     13113.0  United Kingdom  

[495478 rows x 8 columns]

In [11]:
#
df.InvoiceNo.describe()

count     541909
unique     25900
top       573585
freq        1114
Name: InvoiceNo, dtype: int64

In [12]:
#view the first 10 cancelled transactions (InvoiceNo starting with 'C')
df[df['InvoiceNo'].astype(str).str.startswith('C')]['InvoiceNo'].head(10)

141    C536379
154    C536383
235    C536391
236    C536391
237    C536391
238    C536391
239    C536391
240    C536391
241    C536391
939    C536506
Name: InvoiceNo, dtype: object

In [13]:
#viewing negative or zero quantities
df[df['Quantity'] <= 0]

InvoiceNo StockCode                       Description  Quantity  \
141      C536379         D                          Discount        -1   
154      C536383    35004C   SET OF 3 COLOURED  FLYING DUCKS        -1   
235      C536391     22556    PLASTERS IN TIN CIRCUS PARADE        -12   
236      C536391     21984  PACK OF 12 PINK PAISLEY TISSUES        -24   
237      C536391     21983  PACK OF 12 BLUE PAISLEY TISSUES        -24   
...          ...       ...                               ...       ...   
540449   C581490     23144   ZINC T-LIGHT HOLDER STARS SMALL       -11   
541541   C581499         M                            Manual        -1   
541715   C581568     21258        VICTORIAN SEWING BOX LARGE        -5   
541716   C581569     84978  HANGING HEART JAR T-LIGHT HOLDER        -1   
541717   C581569     20979     36 PENCILS TUBE RED RETROSPOT        -5   

               InvoiceDate  UnitPrice  CustomerID         Country  
141    2010-12-01 09:41:00      27.50     14527.0  United Kingdom  
154    2010-12-01 09:49:00       4.65     15311.0  United Kingdom  
235    2010-12-01 10:24:00       1.65     17548.0  United Kingdom  
236    2010-12-01 10:24:00       0.29     17548.0  United Kingdom  
237    2010-12-01 10:24:00       0.29     17548.0  United Kingdom  
...                    ...        ...         ...             ...  
540449 2011-12-09 09:57:00       0.83     14397.0  United Kingdom  
541541 2011-12-09 10:28:00     224.69     15498.0  United Kingdom  
541715 2011-12-09 11:57:00      10.95     15311.0  United Kingdom  
541716 2011-12-09 11:58:00       1.25     17315.0  United Kingdom  
541717 2011-12-09 11:58:00       1.25     17315.0  United Kingdom  

[10624 rows x 8 columns]

In [14]:
#view zero or negative prices
df[df['UnitPrice'] <= 0]

InvoiceNo StockCode                   Description  Quantity  \
622       536414     22139                           NaN        56   
1970      536545     21134                           NaN         1   
1971      536546     22145                           NaN         1   
1972      536547     37509                           NaN         1   
1987      536549    85226A                           NaN         1   
...          ...       ...                           ...       ...   
536981    581234     72817                           NaN        27   
538504    581406    46000M  POLYESTER FILLER PAD 45x45cm       240   
538505    581406    46000S  POLYESTER FILLER PAD 40x40cm       300   
538554    581408     85175                           NaN        20   
538919    581422     23169                       smashed      -235   

               InvoiceDate  UnitPrice  CustomerID         Country  
622    2010-12-01 11:52:00        0.0         NaN  United Kingdom  
1970   2010-12-01 14:32:00        0.0         NaN  United Kingdom  
1971   2010-12-01 14:33:00        0.0         NaN  United Kingdom  
1972   2010-12-01 14:33:00        0.0         NaN  United Kingdom  
1987   2010-12-01 14:34:00        0.0         NaN  United Kingdom  
...                    ...        ...         ...             ...  
536981 2011-12-08 10:33:00        0.0         NaN  United Kingdom  
538504 2011-12-08 13:58:00        0.0         NaN  United Kingdom  
538505 2011-12-08 13:58:00        0.0         NaN  United Kingdom  
538554 2011-12-08 14:06:00        0.0         NaN  United Kingdom  
538919 2011-12-08 15:24:00        0.0         NaN  United Kingdom  

[2517 rows x 8 columns]

In [15]:
#viewing InvoiceDate data type
print("InvoiceDate data type:", df['InvoiceDate'].dtype)

InvoiceDate data type: datetime64[ns]


In [16]:
df.describe(include='all')

InvoiceNo StockCode                         Description  \
count    541909.0    541909                              540455   
unique    25900.0      4070                                4223   
top      573585.0    85123A  WHITE HANGING HEART T-LIGHT HOLDER   
freq       1114.0      2313                                2369   
mean          NaN       NaN                                 NaN   
min           NaN       NaN                                 NaN   
25%           NaN       NaN                                 NaN   
50%           NaN       NaN                                 NaN   
75%           NaN       NaN                                 NaN   
max           NaN       NaN                                 NaN   
std           NaN       NaN                                 NaN   

             Quantity                    InvoiceDate      UnitPrice  \
count   541909.000000                         541909  541909.000000   
unique            NaN                            NaN            NaN   
top               NaN                            NaN            NaN   
freq              NaN                            NaN            NaN   
mean         9.552250  2011-07-04 13:34:57.156386048       4.611114   
min     -80995.000000            2010-12-01 08:26:00  -11062.060000   
25%          1.000000            2011-03-28 11:34:00       1.250000   
50%          3.000000            2011-07-19 17:17:00       2.080000   
75%         10.000000            2011-10-19 11:27:00       4.130000   
max      80995.000000            2011-12-09 12:50:00   38970.000000   
std        218.081158                            NaN      96.759853   

           CustomerID         Country  
count   406829.000000          541909  
unique            NaN              38  
top               NaN  United Kingdom  
freq              NaN          495478  
mean     15287.690570             NaN  
min      12346.000000             NaN  
25%      13953.000000             NaN  
50%      15152.000000             NaN  
75%      16791.000000             NaN  
max      18287.000000             NaN  
std       1713.600303             NaN

**Data Cleaning**


In [17]:
# make a copy of the original dataframe for cleaning
cleaned_df = df.copy()
cleaned_df.head()


InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate  UnitPrice  CustomerID         Country  
0 2010-12-01 08:26:00       2.55     17850.0  United Kingdom  
1 2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
2 2010-12-01 08:26:00       2.75     17850.0  United Kingdom  
3 2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
4 2010-12-01 08:26:00       3.39     17850.0  United Kingdom

In [18]:
#checking for duplicates
duplicate_count = cleaned_df.duplicated().sum()
print(f"Number of duplicate rows: {duplicate_count}")

Number of duplicate rows: 5268


In [19]:
#inspect the duplicate rows (if any)
duplicates = cleaned_df[cleaned_df.duplicated()]
print("Duplicate rows:")
print(duplicates)

Duplicate rows:
       InvoiceNo StockCode                        Description  Quantity  \
517       536409     21866        UNION JACK FLAG LUGGAGE TAG         1   
527       536409     22866      HAND WARMER SCOTTY DOG DESIGN         1   
537       536409     22900    SET 2 TEA TOWELS I LOVE LONDON          1   
539       536409     22111       SCOTTIE DOG HOT WATER BOTTLE         1   
555       536412     22327  ROUND SNACK BOXES SET OF 4 SKULLS         1   
...          ...       ...                                ...       ...   
541675    581538     22068        BLACK PIRATE TREASURE CHEST         1   
541689    581538     23318     BOX OF 6 MINI VINTAGE CRACKERS         1   
541692    581538     22992             REVOLVER WOODEN RULER          1   
541699    581538     22694                       WICKER STAR          1   
541701    581538     23343       JUMBO BAG VINTAGE CHRISTMAS          1   

               InvoiceDate  UnitPrice  CustomerID         Country  
517    2010-12-

In [20]:
#drop duplicates
cleaned_df = cleaned_df.drop_duplicates()
#verify duplicates are removed
duplicate_count_after = cleaned_df.duplicated().sum()
print(f"Number of duplicate rows after removal: {duplicate_count_after}")

Number of duplicate rows after removal: 0


**Standardized Cleaning Pipeline**

In [21]:
#Remove rows without CustomerID (required for RFM)
cleaned_df = cleaned_df.dropna(subset=['CustomerID'])
#Remove cancelled invoices
cleaned_df['InvoiceNo'] = cleaned_df['InvoiceNo'].astype(str) #convert to string for startswith
cleaned_df = cleaned_df[~cleaned_df['InvoiceNo'].str.startswith('C')]
#Remove negative or zero quantities
cleaned_df = cleaned_df[cleaned_df['Quantity'] > 0]
#Remove zero or negative prices
cleaned_df = cleaned_df[cleaned_df['UnitPrice'] > 0]
#Convert CustomerID to integer
cleaned_df['CustomerID'] = cleaned_df['CustomerID'].astype(int)

#Convert InvoiceDate to datetime
cleaned_df['InvoiceDate'] = pd.to_datetime(cleaned_df['InvoiceDate'])

#Standardization Data Types [Convert IDs to string for consistency]
cleaned_df['CustomerID'] = cleaned_df['CustomerID'].astype(str)
cleaned_df['InvoiceNo'] = cleaned_df['InvoiceNo'].astype(str)
cleaned_df['StockCode'] = cleaned_df['StockCode'].astype(str)

#Ensure numeric columns are correct data types
cleaned_df['Quantity'] = cleaned_df['Quantity'].astype(int)
cleaned_df['UnitPrice'] = cleaned_df['UnitPrice'].astype(float)


# Create TotalPrice column needed for RFM
cleaned_df['TotalPrice'] = cleaned_df['Quantity'] * cleaned_df['UnitPrice']
cleaned_df['TotalPrice'] = cleaned_df['TotalPrice'].astype(float)

#Optimize categorical data types
cleaned_df['Country'] = cleaned_df['Country'].astype('category')
cleaned_df['Description'] = cleaned_df['Description'].astype('string')

#drop rows with any remaining missing values (if any)
cleaned_df.dropna(inplace=True)
print("Cleaned dataset shape:", cleaned_df.shape)
cleaned_df.head()

Cleaned dataset shape: (392692, 9)


InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate  UnitPrice CustomerID         Country  TotalPrice  
0 2010-12-01 08:26:00       2.55      17850  United Kingdom       15.30  
1 2010-12-01 08:26:00       3.39      17850  United Kingdom       20.34  
2 2010-12-01 08:26:00       2.75      17850  United Kingdom       22.00  
3 2010-12-01 08:26:00       3.39      17850  United Kingdom       20.34  
4 2010-12-01 08:26:00       3.39      17850  United Kingdom       20.34

In [22]:
#cheking data types after cleaning
cleaned_df.dtypes

InvoiceNo              object
StockCode              object
Description    string[python]
Quantity                int64
InvoiceDate    datetime64[ns]
UnitPrice             float64
CustomerID             object
Country              category
TotalPrice            float64
dtype: object

In [23]:
#describe the numeric columnn of the cleaned dataset
cleaned_df[['UnitPrice', 'Quantity', 'CustomerID', 'TotalPrice']].describe()

UnitPrice       Quantity     TotalPrice
count  392692.000000  392692.000000  392692.000000
mean        3.125914      13.119702      22.631500
std        22.241836     180.492832     311.099224
min         0.001000       1.000000       0.001000
25%         1.250000       2.000000       4.950000
50%         1.950000       6.000000      12.450000
75%         3.750000      12.000000      19.800000
max      8142.750000   80995.000000  168469.600000

In [24]:
#Applying Winsorization Quantile capping (99th percentile)
for col in ['Quantity', 'UnitPrice', 'TotalPrice']:
    lower = cleaned_df[col].quantile(0.01)
    upper = cleaned_df[col].quantile(0.99)
    
    cleaned_df[col] = cleaned_df[col].clip(lower, upper)

print("Outliers capped successfully")

Outliers capped successfully


In [25]:
cleaned_df[['UnitPrice', 'Quantity', 'CustomerID', 'TotalPrice']].describe()

UnitPrice       Quantity     TotalPrice
count  392692.000000  392692.000000  392692.000000
mean        2.833735      11.022402      19.152962
std         2.791717      18.158425      29.701258
min         0.210000       1.000000       0.550000
25%         1.250000       2.000000       4.950000
50%         1.950000       6.000000      12.450000
75%         3.750000      12.000000      19.800000
max        14.950000     120.000000     203.520000

**Extreme transactional values were treated using 1st-99th percentile Winsorization to stabilize**
**distributions while preserving the full transactional dataset.**

**Statistical EDA Data Analysis and Visualization**

In [26]:
#distribution of TotalPrice
plt.figure(figsize=(10, 6))
sns.histplot(data=cleaned_df, x='TotalPrice')
plt.title('Distribution of TotalPrice')
plt.xlabel('TotalPrice')
plt.ylabel('Frequency')
plt.tight_layout()
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/Distribution of TotalPrice.png')

In [27]:
#distribution of UnitPrice
plt.figure(figsize=(10, 6))
sns.histplot(data=cleaned_df, x='UnitPrice')
plt.title('Distribution of UnitPrice')
plt.xlabel('UnitPrice')
plt.ylabel('Frequency')
plt.tight_layout()
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/Distribution of UnitPrice.png')

In [28]:
#distribution of Quantity
plt.figure(figsize=(10, 6))
sns.histplot(cleaned_df, x='Quantity')
plt.title('Distribution of Quantity')
plt.xlabel('Quantity')
plt.ylabel('Frequency')
plt.tight_layout()
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/Distribution of Quantity.png')

In [29]:
#box plot for UnitPrice
fig = px.box(cleaned_df,
             y='UnitPrice',
             title='Box Plot of Unit Price')
# Save as PNG
fig.write_image("/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/unitprice_boxplot.png")

fig.show()

In [30]:
#box plot for quantity
fig = px.box(cleaned_df,
             y='Quantity',
             title='Box Plot of Quantity')  
# Save as PNG
fig.write_image("/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/quantity_boxplot.png")
fig.show()

In [31]:
#box plot for TotalPrice
fig = px.box(cleaned_df,
             y='TotalPrice',
             title='Box Plot of Total Price')
# Save as PNG
fig.write_image("/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/totalprice_boxplot.png")
fig.show()

In [32]:
#top products by total sales
top_products = cleaned_df.groupby('Description')['TotalPrice'].sum().sort_values(ascending=False).head(10)
print("Top 10 products by total sales:")
print(top_products)

Top 10 products by total sales:
Description
REGENCY CAKESTAND 3 TIER              105785.74
WHITE HANGING HEART T-LIGHT HOLDER     70954.55
JUMBO BAG RED RETROSPOT                68504.32
POSTAGE                                66147.35
PARTY BUNTING                          59083.41
ASSORTED COLOUR BIRD ORNAMENT          48047.99
PAPER CHAIN KIT 50'S CHRISTMAS         35700.33
CHILLI LIGHTS                          32536.55
SPOTTY BUNTING                         31618.99
RABBIT NIGHT LIGHT                     31520.96
Name: TotalPrice, dtype: float64


In [33]:
# Plot top 10 products by total sales
plt.figure(figsize=(8,6))  # set figure size

top_products.plot(kind='bar')  # create bar chart

plt.title('Top 10 Products by Total Sales')  # chart title
plt.xlabel('Product Description')  # x-axis label
plt.ylabel('Total Sales')  # y-axis label
plt.xticks(rotation=45, ha='right')  # rotate labels for readability

# Save figure to specified directory
plt.tight_layout()  # adjust layout to prevent cutting labels
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/top_10_products_sales.png')

In [34]:
#top 10 Revenue distribution by country
country_revenue = cleaned_df.groupby('Country')['TotalPrice'].sum().sort_values(ascending=False).head(10)
print("Top 10 countries by revenue:")
print(country_revenue)

Top 10 countries by revenue:
Country
United Kingdom    6119741.19
Netherlands        233512.17
EIRE               225234.61
Germany            220831.16
France             193747.18
Australia          101686.13
Switzerland         55656.41
Spain               53279.25
Belgium             41196.34
Norway              34702.01
Name: TotalPrice, dtype: float64


In [36]:
# Plot top 10 countries by revenue
from matplotlib import ticker


plt.figure(figsize=(10,6))  # set figure size

ax = country_revenue.plot(kind='bar')  # create bar chart

plt.title('Top 10 Countries by Revenue')  # chart title
plt.xlabel('Country')  # x-axis label
plt.ylabel('Total Revenue')  # y-axis label
plt.xticks(rotation=45, ha='right')  # rotate country names

# Format y-axis with commas
ax.yaxis.set_major_formatter(ticker.FuncFormatter(lambda x, pos: f'{int(x):,}'))

plt.tight_layout()  # adjust layout

# Save to outputs directory
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/top_10_countries_revenue.png')

In [55]:
#Correlation between Quantity and TotalPrice heatmap
correlation = cleaned_df[['Quantity', 'TotalPrice']].corr()
plt.figure(figsize=(6,4))
sns.heatmap(correlation, annot=True, cmap='coolwarm', fmt=".2f")
plt.title('Correlation Heatmap: Quantity vs TotalPrice')
plt.tight_layout()
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/correlation_heatmap.png', bbox_inches='tight')

In [37]:
cleaned_df.dtypes

InvoiceNo              object
StockCode              object
Description    string[python]
Quantity                int64
InvoiceDate    datetime64[ns]
UnitPrice             float64
CustomerID             object
Country              category
TotalPrice            float64
dtype: object

**Time series Analysis**

In [39]:
#yearly Revenue Trend  
cleaned_df['Year'] = cleaned_df['InvoiceDate'].dt.to_period('Y')
yearly_revenue = cleaned_df.groupby('Year')['TotalPrice'].sum()
print("Yearly Revenue Trend:")
print(yearly_revenue)

Yearly Revenue Trend:
Year
2010     498162.03
2011    7023052.84
Freq: Y-DEC, Name: TotalPrice, dtype: float64


In [42]:
# Plot yearly revenue trend
plt.figure(figsize=(10,6))
plt.plot(yearly_revenue.index.astype(str), yearly_revenue.values, marker='o', linestyle='-', color='teal')
plt.title('Yearly Revenue Trend')
plt.xlabel('Year')
plt.ylabel('Revenue')
plt.grid(True)

# Save plot as PNG
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/yearly_revenue_trend.png', bbox_inches='tight')

In [49]:
# calcualte distinct month in year for 2010, and 2011
cleaned_df['Month'] = cleaned_df['InvoiceDate'].dt.to_period('M')
months_2010 = cleaned_df[cleaned_df['Year'] == '2010']['Month'].nunique()
months_2011 = cleaned_df[cleaned_df['Year'] == '2011']['Month'].nunique()
print(f"Distinct months in 2010: {months_2010}")
print(f"Distinct months in 2011: {months_2011}")


Distinct months in 2010: 1
Distinct months in 2011: 12


In [47]:
#Top 3 Monthly Revenue Trend for 2011, and 2010

# Filter data for 2011 and 2010
filtered_df_2011 = cleaned_df[cleaned_df['InvoiceDate'].dt.year == 2011]
filtered_df_2010 = cleaned_df[cleaned_df['InvoiceDate'].dt.year == 2010]

# Calculate monthly revenue for each year
monthly_revenue_2011 = filtered_df_2011.groupby('Month')['TotalPrice'].sum()
monthly_revenue_2010 = filtered_df_2010.groupby('Month')['TotalPrice'].sum()

# Get top 3 months for each year
top_months_2011 = monthly_revenue_2011.sort_values(ascending=False).head(3)
top_months_2010 = monthly_revenue_2010.sort_values(ascending=False).head(3)

print("Top 3 Monthly Revenue Trend for 2011:")
print(top_months_2011)
print("\nTop 3 Monthly Revenue Trend for 2010:")
print(top_months_2010)

Top 3 Monthly Revenue Trend for 2011:
Month
2011-11    1052132.37
2011-10     879191.00
2011-09     809732.44
Freq: M, Name: TotalPrice, dtype: float64

Top 3 Monthly Revenue Trend for 2010:
Month
2010-12    498162.03
Freq: M, Name: TotalPrice, dtype: float64


In [74]:
#plot Month and revenue trend for 2011 (all months)
# Convert PeriodIndex to month numbers from monthly_revenue_2011
month_numbers = [m.month for m in monthly_revenue_2011.index]
month_names = [calendar.month_name[m] for m in month_numbers]
plt.figure(figsize=(10,6))
plt.bar(month_names, monthly_revenue_2011.values, color='coral')
plt.title('Monthly Revenue Trend for 2011')
plt.xlabel('Month')
plt.ylabel('Revenue')
plt.xticks(rotation=45, ha='right')
plt.gca().yaxis.set_major_formatter(StrMethodFormatter('{x:,.0f}'))
plt.tight_layout()
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/monthly_revenue_trend_2011.png', bbox_inches='tight')
plt.show()

In [ ]:
#plot top 3 month name and revenue trend for 2011
# Convert PeriodIndex to month numbers
month_numbers = [m.month for m in top_months_2011.index]
month_names = [calendar.month_name[m] for m in month_numbers]

plt.figure(figsize=(10,6))
plt.bar(month_names, top_months_2011.values, color='coral')
plt.title('Top 3 Monthly Revenue Trend for 2011')
plt.xlabel('Month')
plt.ylabel('Revenue')
plt.grid(axis='y')  
plt.gca().yaxis.set_major_formatter(StrMethodFormatter('{x:,.0f}'))  # Format y-axis with commas
plt.tight_layout()  # adjust layout

# Save plot
plt.savefig('/Users/2020m1/Downloads/Github-Repos/Customer-Market-Basket-Analytics/outputs/top_3_monthly_revenue_2011.png', bbox_inches='tight')

plt.show()

In [70]:
#2011 best Quarter revenue genrated 
# Filter data for 2011
df_2011 = cleaned_df[cleaned_df['InvoiceDate'].dt.year == 2011]
# Create a 'Quarter' column
df_2011['Quarter'] = df_2011['InvoiceDate'].dt.to_period('Q')
# Calculate revenue for each quarter
quarterly_revenue_2011 = df_2011.groupby('Quarter')['TotalPrice'].sum()
# Get the best quarter
best_quarter_2011 = quarterly_revenue_2011.sort_values(ascending=False).head(1)
print("Best Quarterly Revenue Trend for 2011:")
print(best_quarter_2011)

Best Quarterly Revenue Trend for 2011:
Quarter
2011Q4    2227340.99
Freq: Q-DEC, Name: TotalPrice, dtype: float64


**RFM Segmentation**

In [ ]:
# Calculate RFM Table with proper column names
snapshot_date = cleaned_df['InvoiceDate'].max() + pd.Timedelta(days=1)

rfm = cleaned_df.groupby('CustomerID').agg({
    'InvoiceDate': lambda x: (snapshot_date - x.max()).days,  # Recency
    'InvoiceNo': 'nunique',  # Frequency
    'TotalPrice': 'sum'      # Monetary
}).reset_index()

# Rename columns
rfm.columns = ['CustomerID', 'Recency', 'Frequency', 'Monetary']

# Preview
print("RFM Table:")
print(rfm.head())

RFM Table:
  CustomerID  Recency  Frequency  Monetary
0      12346      326          1    203.52
1      12347        2          7   4263.92
2      12348       75          4   1760.76
3      12349       19          1   1661.07
4      12350      310          1    334.40


In [ ]:
# Build RFM Table
snapshot_date = cleaned_df['InvoiceDate'].max() + pd.Timedelta(days=1)

rfm = cleaned_df.groupby('CustomerID').agg({
    'InvoiceDate': lambda x: (snapshot_date - x.max()).days,  # Recency
    'InvoiceNo': 'nunique',  # Frequency
    'TotalPrice': 'sum'       # Monetary
}).reset_index()

rfm.columns = ['CustomerID', 'Recency', 'Frequency', 'Monetary']

#  Calculate RFM Scores
def rfm_score(x):
    # Recency score
    if x['Recency'] <= 30:
        r = 5
    elif x['Recency'] <= 60:
        r = 4
    elif x['Recency'] <= 90:
        r = 3
    elif x['Recency'] <= 180:
        r = 2
    else:
        r = 1

    # Frequency score
    if x['Frequency'] >= 10:
        f = 5
    elif x['Frequency'] >= 7:
        f = 4
    elif x['Frequency'] >= 4:
        f = 3
    elif x['Frequency'] >= 1:
        f = 2
    else:
        f = 1

    # Monetary score
    if x['Monetary'] >= 1000:
        m = 5
    elif x['Monetary'] >= 500:
        m = 4
    elif x['Monetary'] >= 100:
        m = 3
    elif x['Monetary'] >= 1:
        m = 2
    else:
        m = 1

    return pd.Series([r, f, m], index=['R_Score', 'F_Score', 'M_Score'])

# Apply scoring
rfm[['R_Score', 'F_Score', 'M_Score']] = rfm.apply(rfm_score, axis=1)

# Combine into single RFM Score
rfm['RFM_Score'] = rfm['R_Score'].astype(str) + \
                   rfm['F_Score'].astype(str) + \
                   rfm['M_Score'].astype(str)

# Segment customers (text labels only)
def segment_customer(row):
    if row['R_Score'] >= 4 and row['F_Score'] >= 4 and row['M_Score'] >= 4:
        return 'VIP'
    elif row['R_Score'] >= 3 and row['F_Score'] >= 3:
        return 'Loyal'
    elif row['R_Score'] <= 2 and row['F_Score'] <= 2:
        return 'At-Risk'
    else:
        return 'Potential'

rfm['Segment'] = rfm.apply(segment_customer, axis=1)

# Preview first 10 rows
rfm.head(10)

CustomerID  Recency  Frequency  Monetary  R_Score  F_Score  M_Score  \
0      12346      326          1    203.52        1        2        3   
1      12347        2          7   4263.92        5        4        5   
2      12348       75          4   1760.76        3        3        5   
3      12349       19          1   1661.07        5        2        5   
4      12350      310          1    334.40        1        2        3   
5      12352       36          8   2256.53        4        4        5   
6      12353      204          1     89.00        1        2        2   
7      12354      232          1   1079.40        1        2        5   
8      12355      214          1    459.40        1        2        3   
9      12356       23          3   2690.95        5        2        5   

  RFM_Score    Segment  
0       123    At-Risk  
1       545        VIP  
2       335      Loyal  
3       525  Potential  
4       123    At-Risk  
5       445        VIP  
6       122    At-Risk  
7       125    At-Risk  
8       123    At-Risk  
9       525  Potential

- Customer 12347 (VIP)
- Last purchase 2 days ago = Recency score 5
- 7 invoices = Frequency score 4
- Spent £4263.92 = Monetary score 5
- Highly engaged, high-value customer

In [90]:
#Customer Segments Based on RFM
segment_counts = rfm['Segment'].value_counts()
print("Customer Segments Based on RFM:")
print(segment_counts)


Customer Segments Based on RFM:
Segment
Potential    1673
At-Risk      1306
Loyal         715
VIP           644
Name: count, dtype: int64


**Market Basket Analysis – Prepare Data**

In [93]:
#Market Basket Analysis – Prepare Data
# Group items by InvoiceNo and create a list of items for each transaction
basket = cleaned_df.groupby(['InvoiceNo', 'Description'])['Quantity'].sum().unstack().fillna(0)
# Convert to 0/1 (1 if item bought in that invoice)
basket = basket.applymap(lambda x: 1 if x > 0 else 0)
basket.iloc[0:5, 0:5]

Description  4 PURPLE FLOCK DINNER CANDLES  50'S CHRISTMAS GIFT BAG LARGE  \
InvoiceNo                                                                   
536365                                   0                              0   
536366                                   0                              0   
536367                                   0                              0   
536368                                   0                              0   
536369                                   0                              0   

Description  DOLLY GIRL BEAKER  I LOVE LONDON MINI BACKPACK  \
InvoiceNo                                                     
536365                       0                            0   
536366                       0                            0   
536367                       0                            0   
536368                       0                            0   
536369                       0                            0   

Description  I LOVE LONDON MINI RUCKSACK  
InvoiceNo                                 
536365                                 0  
536366                                 0  
536367                                 0  
536368                                 0  
536369                                 0

In [ ]:
#Run Apriori & Find Frequent Itemsets
frequent_itemsets = apriori(basket, min_support=0.01, use_colnames=True)
frequent_itemsets.sort_values(by='support', ascending=False).head(10)
